In [ ]:
## Si premiere utilisation !!!!

        # Mise a jour des packages

include("miseAjourPackage.jl")

In [55]:
# initialisation des packages necessaires
include("Mnist\\initialisation.jl")

In [56]:
# General initialisation
include("Mnist\\MLP\\initialisation.jl")

In [57]:
#### Backend for plots

# gr()
plotlyjs()

Plots.PlotlyJSBackend()

# Suvegrade all tests

In [58]:
everyTests = []

Any[]

# Ensemble de tests

In [59]:
# fonctions sauvegarde 
include("saveConfig.jl")

testConfig = "testConfiguration.json"
io = open(testConfig, "w")

write(io, "\n#################### Test MNIST : Multilayer Perceptron ############################## \n")

89

In [60]:
# Choix du modele 
TYPE = Float64

##################### definition du modele #################
smallModel = ChainMLP{TYPE}(Layer1(784,10,identity))

mediumModel = ChainMLP{TYPE}( Layer1(784,100,relu),  Layer1(100,10,identity))
mediumModelSigm = ChainMLP{TYPE}( Layer1(784,100,sigm),  Layer1(100,10,identity))

mediumModel2 = ChainMLP{TYPE}( Layer1(784,100, relu), Layer1(100,50, relu), Layer1(50,10,identity))
mediumModelSigm2 = ChainMLP{TYPE}( Layer1(784,100,sigm), Layer1(100,50,sigm), Layer1(50,10,identity))

bigModel = ChainMLP{TYPE}(Layer1(784,500,relu), Layer1(500,100,relu), Layer1(100,10,identity))
bigModelSigm = ChainMLP{TYPE}(Layer1(784,500,sigm), Layer1(500,100,sigm), Layer1(100,10,identity))


veryBigModel = ChainMLP{TYPE}(Layer1(784,600,relu), Layer1(600,500,relu), Layer1(500,400,relu), Layer1(400,300,relu), Layer1(300,200,relu), Layer1(200,100,relu), Layer1(100,10,identity))
veryBigModelSigm = ChainMLP{TYPE}(Layer1(784,600,sigm), Layer1(600,500,sigm), Layer1(500,400,sigm), Layer1(400,300,sigm), Layer1(300,200,sigm), Layer1(200,100,sigm), Layer1(100,10,identity));

In [61]:
# fonction sauvegarde choix modele

function full_setting_model(chain::AbstractChain)
    setting = "\n## Model ##\n"
    setting = string(setting, " + Number of parameters: $(chain.size_model)\n")
    setting = string(setting, " + Layers: \n")
    num = 1
    for layer in chain.layers
        setting = string(setting, "   --> layer $(num): ",  full_setting_layer(layer))
        num += 1
    end
    return setting
end

function full_setting_layer(layer::Layer1)
    o, i = size(layer.w)
   return "input=$(i) / output=$(o) / activation=$(layer.f) \n" 
end

full_setting_layer (generic function with 1 method)

In [62]:
##########  Choix modele ###############
myModel = smallModel


#### sauvegarde ####
setting = full_setting_model(myModel)
println(setting)
write(io, setting)


## Model ##
 + Number of parameters: 7850
 + Layers: 
   --> layer 1: input=784 / output=10 / activation=identity 



116

In [63]:
############# initialisation ##############
dist = Normal(5,20)

random = true

write(io , "\n### Initilisation ### \n")

x0 = create_vector(myModel)

if random
    # ---- Random ----
    write(io, " -- Random : $(dist)\n")
    rand!(dist, x0)
else
   write(io, " -- Xavier uniform \n") 
end

####### definition du modele #######
mnistModel = MnistModel(myModel, x0 , dtrn, dtst)

MnistModel{Float64,Int64}(ChainMLP{Float64}((Layer1(P(Array{Float64,2}(10,784)), P(Array{Float64,1}(10)), identity),), 7850), [25.944241687032147, 10.752778207090794, 8.03669531918356, -8.762830246093083, -1.1981877514077848, 32.38402567841262, -2.991250441480604, -0.21135083690013268, -0.7964204281889495, -9.801007258742578  …  7.955665458147585, -18.55980775833853, 7.142570379607514, 22.711059344522617, -13.48966926998149, 14.715604226762037, 17.308095307442116, 10.849587010642075, 14.743075271671245, -8.583073909679674], MnistDataMLP{Float64,Int64}([0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0; … ; 0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0], [6, 5, 8, 3, 8, 6, 4, 8, 2, 3  …  4, 1, 4, 1, 7, 9, 1, 6, 1, 1], 1), MnistDataMLP{Float64,Int64}([0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0; … ; 0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0], [7, 2, 1, 10, 4, 1, 4, 9, 5, 9  …  7, 8, 9, 10, 1, 2, 3, 4, 5, 6], 10000), Geraldine.Unconstraint())

# Definition des fonctions

In [64]:

    function lancementTest(test::SecondOrderTest, allTests::AllTests)

        _, acc =  test.algo(allTests.model, allTests.x0, test.sam ; b = test.b, 
                            verbose = test.verbose, accumulator = test.accumulator)

        data = (getData(acc))

        if (typeof(test.sam) <: Union{Geraldine.AbstractRandomDynamicTrueVar, Geraldine.AbstractTrueVarSAA})
            append!(allTests.all_dataVariance, [data])

            # Accuracy arrays
            acc_test = computeAccTest(allTests.model, data)
            append!(allTests.all_accuracy_testVariance, [acc_test])
        else
            append!(allTests.all_dataNormal, [data])

            # Accuracy arrays
            acc_test = computeAccTest(allTests.model, data)
            append!(allTests.all_accuracy_testNormal, [acc_test])
        end

    end

    function lancementTest(test::FirstOrderTest, allTests::AllTests)

        _, acc = test.algo(allTests.model, test.state ; 
                            verbose = test.verbose, accumulator = test.accumulator, sp = test.sp)


        data = (getData(acc))

        append!(allTests.all_dataNormal, [data])

        # Accuracy arrays
        acc_test = computeAccTest(allTests.model, data)
        append!(allTests.all_accuracy_testNormal, [acc_test])
    end

    function lancementAllTests(tests::Array{Test, 1}, allTests::AllTests)
        for test in tests
           lancementTest(test, allTests) 
        end
    end


lancementAllTests (generic function with 1 method)

# Structure des tests

In [65]:
 alltests = AllTests(mnistModel, mnistModel.x0)

AllTests{Float64}(MnistModel{Float64,Int64}(ChainMLP{Float64}((Layer1(P(Array{Float64,2}(10,784)), P(Array{Float64,1}(10)), identity),), 7850), [25.944241687032147, 10.752778207090794, 8.03669531918356, -8.762830246093083, -1.1981877514077848, 32.38402567841262, -2.991250441480604, -0.21135083690013268, -0.7964204281889495, -9.801007258742578  …  7.955665458147585, -18.55980775833853, 7.142570379607514, 22.711059344522617, -13.48966926998149, 14.715604226762037, 17.308095307442116, 10.849587010642075, 14.743075271671245, -8.583073909679674], MnistDataMLP{Float64,Int64}([0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0; … ; 0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0], [6, 5, 8, 3, 8, 6, 4, 8, 2, 3  …  4, 1, 4, 1, 7, 9, 1, 6, 1, 1], 1), MnistDataMLP{Float64,Int64}([0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0; … ; 0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0], [7, 2, 1, 10, 4, 1, 4, 9, 5, 9  …  7, 8, 9, 10, 1, 2, 3, 4, 5, 6], 10000), Geraldine.Unconstraint()), [25.944241687032147, 10.752778207090794, 8.03669531918356, -8

# BTR

In [66]:
#####################################################################################
# Optimisation
verbose = false

IterMax = 50
TMax = 7200.0 # 15 minutes
epsilonOptimisation = 10^(-6)

# Sampling init
N0 = 100
NMin = 50
increment = 2;

# subSampling
coeff_bhhh = 0.1
maxBhhh = 5000
subSampling = ConstantCoeffSubSampling(maxBhhh, coeff_bhhh)

#btrCoeffs = Geraldine.BTRDefaults() # avec 4*‖s‖
btrCoeffs = Geraldine.BTRDefaultsCoeff() # avec expension de γ_3 pour iteration tres reussie

Geraldine.BasicTrustRegionWithCoeff{Float64}(0.01, 0.8, 0.5, 0.9, 1.5)

## With True variance

In [67]:
# Test 1: BHHH

# BHHH 
Hessian = Geraldine.BHHHScores{TYPE}

# smoothing = Geraldine.NoSmoothing()
# smoothing = Geraldine.CumulativeDecreaseSmoothing{Float64}(; maxIter=3)
smoothing = Geraldine.NaiveSmoothing()

commonVar = true
sam = RandomSamplingDynamicTrueVariance(NMin = NMin, NMax = Nobs(mnistModel), N0=N0, increment=increment, 
                                                    commonVar = commonVar,
                                                    smoothing=smoothing, 
                                                    subSampling=subSampling)

mybtr = BTRStruct(;sam = typeof(sam), Hessian = Hessian, eps = epsilonOptimisation, Nmax = IterMax, TMax = TMax);
        
test = SecondOrderTest(mybtr, sam, btrCoeffs; verbose = verbose);

addTest(test, alltests)

sam

RandomSamplingDynamicTrueVariance(100, 50, 50, 100, 60000, #undef, true, Geraldine.NaiveSmoothing(0.75, 2.0), ConstantCoeffSubSampling(5000, 0.1), 2, 0.05, 1.6448536269514717)

In [68]:
# Test 2: DiagBHHH

# Hessian 
Hessian = Geraldine.DiagBHHHApprox{TYPE}

# smoothing = Geraldine.NoSmoothing()
# smoothing = Geraldine.CumulativeDecreaseSmoothing{Float64}(; maxIter=3)
smoothing = Geraldine.NaiveSmoothing()

commonVar = true
sam = RandomSamplingDynamicTrueVariance(NMin = NMin, NMax = Nobs(mnistModel), N0=N0, increment=increment, 
                                                    commonVar = commonVar,
                                                    smoothing=smoothing, 
                                                    subSampling=subSampling)

mybtr = BTRStruct(;sam = typeof(sam), Hessian = Hessian, eps = epsilonOptimisation, Nmax = IterMax, TMax = TMax);
        
test = SecondOrderTest(mybtr, sam, btrCoeffs; verbose = verbose);

addTest(test, alltests)


sam

RandomSamplingDynamicTrueVariance(100, 50, 50, 100, 60000, #undef, true, Geraldine.NaiveSmoothing(0.75, 2.0), ConstantCoeffSubSampling(5000, 0.1), 2, 0.05, 1.6448536269514717)

In [69]:
# Test 3

# Hessian 
Hessian = Geraldine.IdentityApprox{TYPE}

# smoothing = Geraldine.NoSmoothing()
# smoothing = Geraldine.CumulativeDecreaseSmoothing{Float64}(; maxIter=3)
smoothing = Geraldine.NaiveSmoothing()

commonVar = true
sam = RandomSamplingDynamicTrueVariance(NMin = NMin, NMax = Nobs(mnistModel), N0=N0, increment=increment, 
                                                    commonVar = commonVar,
                                                    smoothing=smoothing, 
                                                    subSampling=subSampling)

mybtr = BTRStruct(;sam = typeof(sam), Hessian = Hessian, eps = epsilonOptimisation, Nmax = IterMax, TMax = TMax);
        
test = SecondOrderTest(mybtr, sam, btrCoeffs; verbose = verbose);

addTest(test, alltests)

sam

RandomSamplingDynamicTrueVariance(100, 50, 50, 100, 60000, #undef, true, Geraldine.NaiveSmoothing(0.75, 2.0), ConstantCoeffSubSampling(5000, 0.1), 2, 0.05, 1.6448536269514717)

In [70]:
# Test 4

# Hessian 
Hessian = Geraldine.DiagAdamApprox{TYPE}

# smoothing = Geraldine.NoSmoothing()
# smoothing = Geraldine.CumulativeDecreaseSmoothing{Float64}(; maxIter=3)
smoothing = Geraldine.NaiveSmoothing()

commonVar = true
sam = RandomSamplingDynamicTrueVariance(NMin = NMin, NMax = Nobs(mnistModel), N0=N0, increment=increment, 
                                                    commonVar = commonVar,
                                                    smoothing=smoothing, 
                                                    subSampling=subSampling)

mybtr = BTRStruct(;sam = typeof(sam), Hessian = Hessian, eps = epsilonOptimisation, Nmax = IterMax, TMax = TMax);
        
test = SecondOrderTest(mybtr, sam, btrCoeffs; verbose = verbose);

addTest(test, alltests)


sam

RandomSamplingDynamicTrueVariance(100, 50, 50, 100, 60000, #undef, true, Geraldine.NaiveSmoothing(0.75, 2.0), ConstantCoeffSubSampling(5000, 0.1), 2, 0.05, 1.6448536269514717)

## With sHs 

In [71]:
# Test 4

# Hessian 
Hessian = Geraldine.BHHHScores{TYPE}

# smoothing = Geraldine.NoSmoothing()
# smoothing = Geraldine.CumulativeDecreaseSmoothing{Float64}(; maxIter=3)
smoothing = Geraldine.NaiveSmoothing()

commonVar = true
sam = RandomSamplingDynamic(NMin = NMin, NMax = Nobs(mnistModel), N0=N0, increment=increment, 
                                                    commonVar = commonVar,
                                                    smoothing=smoothing, 
                                                    subSampling=subSampling)

mybtr = BTRStruct(;sam = typeof(sam), Hessian = Hessian, eps = epsilonOptimisation, Nmax = IterMax, TMax = TMax);
        
test = SecondOrderTest(mybtr, sam, btrCoeffs; verbose = verbose);

addTest(test, alltests)

sam

RandomSamplingDynamic(100, 50, 50, 100, 60000, #undef, true, Geraldine.NaiveSmoothing(0.75, 2.0), ConstantCoeffSubSampling(5000, 0.1), 2, 0.05, 1.6448536269514717)

# First-Order

In [72]:
##################################################
verbose = false

IterMax = 50
TMax = 300.0

sizeBatch = 100

epsOptimisation = 10^(-6)

sp = Geraldine.StopParam(;NMax = IterMax, TMax = TMax, tol = epsOptimisation);

sam = RandomSampling(;N = sizeBatch, NMax=Nobs(mnistModel))

RandomSampling(100, 60000, #undef)

In [73]:
# Test Adam 1

state = AdamState(mnistModel.x0, sam)

α_adam = 0.01
β_1 = 0.9
β_2 = 0.999

algo = AdamConstStep(α_adam, β_1, β_2)

# Creation test
test = FirstOrderTest(state, sam, algo, sp; verbose = verbose);

# Enregistrement test
addTest(test, alltests);

In [74]:
# Test Adam 2

state = AdamState(mnistModel.x0, sam)

α_adam = 0.0001
β_1 = 0.9
β_2 = 0.999

algo = AdamConstStep(α_adam, β_1, β_2)

# Creation test
test = FirstOrderTest(state, sam, algo, sp; verbose = verbose);

# Enregistrement test
addTest(test, alltests);

In [75]:
# Test Adam 1

state = AdamState(mnistModel.x0, sam)

α_adam = 0.5
β_1 = 0.9
β_2 = 0.999

algo = AdamConstStep(α_adam, β_1, β_2)

# Creation test
test = FirstOrderTest(state, sam, algo, sp; verbose = verbose);

# Enregistrement test
addTest(test, alltests);

In [76]:
# Test SGD 1

state = SGDState(mnistModel.x0, sam)

α_sgd = 0.01

algo = SGDConstStep(α_sgd)

# Creation test
test = FirstOrderTest(state, sam, algo, sp; verbose = verbose);

# Enregistrement test
addTest(test, alltests);

In [77]:
# Test SGD 2

state = SGDState(mnistModel.x0, sam)

α_sgd = 0.5

algo = SGDConstStep(α_sgd)

# Creation test
test = FirstOrderTest(state, sam, algo, sp; verbose = verbose);

# Enregistrement test
addTest(test, alltests);

# Verif tests

In [78]:
println(alltests)

### Tests with TRUE Variance: 
 - T1: BTR-bhhh (VAI/VAC-tv) Naive(0.75, 2.0)
 - T2: BTR-D-bhhh (VAI/VAC-tv) Naive(0.75, 2.0)
 - T3: TR-SGD (VAI/VAC-tv) Naive(0.75, 2.0)
 - T4: BTR-D-Adam (VAI/VAC-tv) Naive(0.75, 2.0)
### Tests with sHs: 
 - T5: BTR-bhhh (VAI/VAC sHs) Naive(0.75, 2.0)
 - T6: Adam (VAI N=100) α=0.01
 - T7: Adam (VAI N=100) α=0.0001
 - T8: Adam (VAI N=100) α=0.5
 - T9: SGD (VAI N=100) α=0.01
 - T10: SGD (VAI N=100) α=0.5


# Lancement de tests

In [79]:
# F normal 

@eval (Sofia.F(x::Vector, mo::MnistModel; sample::AbstractVector{Int64} = 1:Nobs(mo)) = F_normal(x, mo; sample=sample))
lancementAllTests(alltests.testsNormal, alltests)

# F variance
@eval (Sofia.F(x::Vector, mo::MnistModel; sample::AbstractVector{Int64} = 1:Nobs(mo)) = F_variance(x, mo; sample=sample))
lancementAllTests(alltests.testsVariance, alltests)


------ Classic btr ---------- : 
 --- sampling : RandomSamplingDynamic
 --- smoothing : Geraldine.NaiveSmoothing(0.75, 2.0)
-------------------------
initializeState! AbstractStochasticModel
nmaxReached
Algorithm of type : AdamConstStep{Float64}
nmaxReached
Algorithm of type : AdamConstStep{Float64}
nmaxReached
Algorithm of type : AdamConstStep{Float64}
nmaxReached
Algorithm of type : SGDConstStep{Float64}
nmaxReached
Algorithm of type : SGDConstStep{Float64}
nmaxReached
 ------- Debut algo btr True Variance ------ : 
 --- sampling : RandomSamplingDynamicTrueVariance
 --- smoothing : Geraldine.NaiveSmoothing(0.75, 2.0)
-------------------------
initializeState! for TRUE Variance
nmaxReached
 ------- Debut algo btr True Variance ------ : 
 --- sampling : RandomSamplingDynamicTrueVariance
 --- smoothing : Geraldine.NaiveSmoothing(0.75, 2.0)
-------------------------
initializeState! for TRUE Variance
nmaxReached
 ------- Debut algo btr True Variance ------ : 
 --- sampling : RandomSampli

In [80]:
lines = [:solid, :dot, :dash, :dashdot]

4-element Array{Symbol,1}:
 :solid
 :dot
 :dash
 :dashdot

In [81]:
p = plot(xlabel="iterations", ylabel="Accuracy on test set (%)", legend=:bottom)

for i in 1:length(alltests.testsVariance)
    plot!(alltests.all_dataVariance[i].IterAccumulator, alltests.all_accuracy_testVariance[i], 
            label = alltests.all_legendVariance[i], line=lines[i%4 + 1])
end

for i in 1:length(alltests.testsNormal)
    plot!(alltests.all_dataNormal[i].IterAccumulator, alltests.all_accuracy_testNormal[i], 
        label = alltests.all_legendNormal[i], line=lines[i%4 + 1])
end

savefig(p, "comparaison_all_methods_iter.svg")


p

<!DOCTYPE html>
 
 
 Plots.jl

In [ ]:
p = plot(xlabel="Time (s)", ylabel="Accuracy on test set (%)", legend=:bottom)

for i in 1:length(alltests.testsVariance)
    plot!(alltests.all_dataVariance[i].Times, alltests.all_accuracy_testVariance[i], 
        label = alltests.all_legendVariance[i], line=lines[i%4 + 1])
end

for i in 1:length(alltests.testsNormal)
    plot!(alltests.all_dataNormal[i].Times, alltests.all_accuracy_testNormal[i], 
        label = alltests.all_legendNormal[i], line=lines[i%4 + 1])
end

savefig(p, "comparaison_all_methods_time.svg")

p

In [ ]:
indicesVariance = 1:4
indicesNormal = 1:1


p_sample = plot(xlabel="iterations", ylabel="Sample Size")

for i in indicesVariance
    plot!(p_sample, alltests.all_dataVariance[i].IterAccumulator, alltests.all_dataVariance[i].SamplingSizeAccumulator[1], 
            label = alltests.all_legendVariance[i], line=lines[i%4 + 1])
end

for i in indicesNormal
    plot!(p_sample, alltests.all_dataNormal[i].IterAccumulator, alltests.all_dataNormal[i].SamplingSizeAccumulator[1], 
        label = alltests.all_legendNormal[i], line=lines[i%4 + 1])
end

p_sample

In [ ]:
for i in 1:length(alltests.all_settingNormal)
   write(io, alltests.all_settingNormal[i]) 
end

In [ ]:
for i in 1:length(alltests.all_settingVariance)
   write(io, alltests.all_settingVariance[i]) 
end

In [ ]:
close(io)

# Sauvegarde tous les tests

In [ ]:
append!(everyTests, [alltests]);

In [ ]:
test1 = everyTests[1]

## Sauvegarde tests

In [68]:
# Sauvegarde all tests
all_data = []
all_setting = []
all_legend = []

all_acc_train = []
all_acc_test = []

numberTest = 0

0

# Tests BTR

In [69]:
#####################################################################################
# Optimisation
verbose = false

epsilonOptimisation = 10^(-6)

# Sampling init
N0 = 100
NMin = 50
increment = 2;

# subSampling
coeff_bhhh = 0.1
maxBhhh = 1000
subSampling = ConstantCoeffSubSampling(maxBhhh, coeff_bhhh)

#btrCoeffs = Geraldine.BTRDefaults() # avec 4*‖s‖
btrCoeffs = Geraldine.BTRDefaultsCoeff() # avec expension de γ_3 pour iteration tres reussie

Geraldine.BasicTrustRegionWithCoeff{Float64}(0.01, 0.8, 0.5, 0.9, 1.5)

In [70]:
# definition des fonctions generales
include("Atom\\MLPMnist\\testsBTR\\definitionFunctions.jl")

## -- True variance

In [71]:
# definition des fonctions TRUE Variance
include("Atom\\MLPMnist\\testsBTR\\ensemblesTestsTrueVar.jl")

Accum_tv (generic function with 1 method)

In [72]:
Hessian = Geraldine.BHHHScores{Float64}

BHHHScores{Float64}

In [73]:
IterMax = 10
TMax = 7200.0 # 15 minutes

# smoothing = Geraldine.NoSmoothing()
# smoothing = Geraldine.CumulativeDecreaseSmoothing{Float64}(; maxIter=3)
smoothing = Geraldine.NaiveSmoothing()

commonVar = true
sam = RandomSamplingDynamicTrueVariance(NMin = NMin, NMax = Nobs(mnistModel), N0=N0, increment=increment, 
                                                    commonVar = commonVar,
                                                    smoothing=smoothing, 
                                                    subSampling=subSampling)

mybtr = BTRStruct(;sam = typeof(sam), Hessian = Hessian, eps = epsilonOptimisation, Nmax = IterMax, TMax = TMax);
        
sam

RandomSamplingDynamicTrueVariance(100, 50, 50, 100, 60000, #undef, true, Geraldine.NaiveSmoothing(0.75, 2.0), ConstantCoeffSubSampling(1000, 0.1), 2, 0.05, 1.6448536269514717)

In [74]:
numberTest += 1
append!(all_setting, [full_settings_secondOrder(numberTest, mybtr, btrCoeffs, sam)])
append!(all_legend, [legend_settings_secondOrder(numberTest, mybtr, sam)])

1-element Array{Any,1}:
 "T1: BTR-bhhh (VAI/VAC-tv) Naive(0.75, 2.0)"

In [75]:
_, acc =  mybtr(mnistModel, mnistModel.x0, sam, b = btrCoeffs, verbose = verbose, accumulator = Accum_tv());

data = (getData(acc))

append!(all_data, [data]);

 ------- Debut algo btr True Variance ------ : 
 --- sampling : RandomSamplingDynamicTrueVariance
 --- smoothing : Geraldine.NaiveSmoothing(0.75, 2.0)
-------------------------
initializeState! for TRUE Variance
--- TCG classic 
--- TCG classic 
--- TCG classic 
--- TCG classic 
--- TCG classic 
--- TCG classic 
--- TCG classic 
--- TCG classic 
--- TCG classic 
--- TCG classic 
nmaxReached


In [76]:
# Accuracy arrays

# acc_train = computeAccTrain(mnistModel, data)
acc_test = computeAccTest(mnistModel, data)

# append!(all_acc_train, [acc_train])
append!(all_acc_test, [acc_test])

1-element Array{Any,1}:
 Any[8.32, 9.58, 15.1, 23.47, 26.41, 28.21, 42.699999999999996, 48.29, 48.29, 55.96, 66.33]

In [150]:
p_sample = plot(xlabel="", ylabel="Sample size")
plot!(p_sample, all_data[end].IterAccumulator, all_data[end].SamplingSizeAccumulator, label = "")

p_acc = plot(xlabel="iterations", ylabel="Distance to solution")
plot!(p_acc, all_data[end].IterAccumulator, all_acc_test[end], label = all_legend[end])

p = plot(p_sample, p_acc, layout=(2,1), legend=:bottomright)

# savefig(p, "graph_test_$(numberTest).svg") # 

p

<!DOCTYPE html>
 
 
 Plots.jl

### Comparaison second-order

In [151]:
indices = [1,2,4,6]

4-element Array{Int64,1}:
 1
 2
 4
 6

In [152]:
p_sample = plot(xlabel="iterations", ylabel="Sample Sizes")

for i in indices
    plot!(p_sample, all_data[i].IterAccumulator, all_data[i].SamplingSizeAccumulator, label = all_legend[i])
end

# savefig(p_sample, "comparaison_sampleSize_second-order_BHHH.svg")

p_sample

<!DOCTYPE html>
 
 
 Plots.jl

In [153]:
p_sample = plot(xlabel="", ylabel="Sample Sizes")

for i in indices
    plot!(p_sample, all_data[i].Times, all_data[i].SamplingSizeAccumulator, label = "")
end

p_acc = plot(xlabel="Time (s)", ylabel="Accuracy on test set (%)")
for i in indices 
    plot!(p_acc, all_data[i].Times, all_acc_test[i], label = all_legend[i])
end

p = plot(p_sample, p_acc, layout=(2,1), legend=:bottom)

# savefig(p, "comparaison_times_second-order_BHHH.svg")

p

<!DOCTYPE html>
 
 
 Plots.jl

In [154]:
p_sample = plot(xlabel="", ylabel="Sample Sizes")

for i in indices
    plot!(p_sample, all_data[i].IterAccumulator, all_data[i].SamplingSizeAccumulator, label = "")
end

p_acc = plot(xlabel="iterations", ylabel="Accuracy on test set (%)")
for i in indices 
    plot!(p_acc, all_data[i].IterAccumulator, all_acc_test[i], label = all_legend[i])
end

p = plot(p_sample, p_acc, layout=(2,1), legend=:bottom)

# savefig(p, "comparaison_iter_second-order_BHHH.svg")

p

<!DOCTYPE html>
 
 
 Plots.jl

#### Other informations

In [155]:

p_delta = plot(xlabel="", ylabel="Trust region Δ", ylims=(-0.2, 2.0), legend=:top)
for i in indices
    plot!(p_delta, all_data[i].IterAccumulator, all_data[i].DeltaAccumulator, label = all_legend[i])
end

p_dist = plot(xlabel="iterations", ylabel="Accuracy test set (%)")
for i in indices
    plot!(p_dist, all_data[i].IterAccumulator, all_acc_test[i], label = "")
end

p = plot(p_delta, p_dist, layout=(2,1), legend=:top)

# savefig(p, "deltas_distTo_bhhh.svg")
# 
p

<!DOCTYPE html>
 
 
 Plots.jl

## First-order

In [156]:
##################################################
verbose = false

IterMax = 1000
TMax = 300.0

epsOptimisation = 10^(-6)

sp = Geraldine.StopParam(;NMax = IterMax, TMax = TMax, tol = epsOptimisation);

In [12]:
include("Atom\\MLPMnist\\testsFirstOrder\\defintionFunctions.jl")

In [158]:
sizeBatch = 100
sam = RandomSampling(;N = sizeBatch, NMax=Nobs(mnistModel))

state = AdamState(mnistModel.x0, sam)
# state = SGDState(x0, sam)
# α_sgd = 0.01

α_adam = 0.0001
β_1 = 0.9
β_2 = 0.999

algo = AdamConstStep(α_adam, β_1, β_2)
# algo = SGDConstStep(α_sgd)

AdamConstStep{Float64}(0.0001, 0.9, 0.999, 1.0e-8)

In [159]:
numberTest += 1
append!(all_setting, [full_settings_firstOrder(numberTest, algo, state, sp)])
append!(all_legend, [legend_settings_firstOrder(numberTest, algo, sam)])

7-element Array{Any,1}:
 "T1: TR-SGD (VAI/VAC-tv) Naive(0.75, 2.0)"
 "T2: BTR-D-bhhh (VAI/VAC-tv) Naive(0.75, 2.0)"
 "T3: SGD (VAI N=100) α=0.01"
 "T4: BTR-D-Adam (VAI/VAC-tv) Naive(0.75, 2.0)"
 "T5: Adam (VAI N=100) α=0.01"
 "T6: BTR-bhhh (VAI/VAC-tv) Naive(0.75, 2.0)"
 "T7: Adam (VAI N=100) α=0.0001"

In [160]:
_, acc = algo(mnistModel, state ; verbose = verbose, accumulator = Accum_fo(), sp = sp)

data = (getData(acc));

append!(all_data, [data]);

Algorithm of type : AdamConstStep{Float64}
nmaxReached


In [161]:
# Accuracy arrays

# acc_train = computeAccTrain(mnistModel, data)
acc_test = computeAccTest(mnistModel, data)

# append!(all_acc_train, [acc_train])
append!(all_acc_test, [acc_test])

7-element Array{Any,1}:
 Any[9.74, 11.85, 14.7, 15.78, 17.01, 17.98, 22.919999999999998, 30.620000000000005, 30.620000000000005, 34.58  …  95.96000000000001, 95.88, 95.86, 95.84, 95.88, 95.83, 95.92, 95.69, 95.95, 95.95]
 Any[9.74, 11.03, 14.29, 22.71, 35.92, 40.42, 45.17, 46.79, 45.79, 45.79  …  95.99, 96.06, 96.03, 96.16, 96.07, 96.14, 96.13000000000001, 96.12, 96.16, 96.16]
 Any[9.74, 10.13, 10.38, 10.7, 11.03, 11.26, 11.77, 11.959999999999999, 12.27, 12.690000000000001  …  87.2, 87.21, 87.29, 87.26, 87.36, 87.33999999999999, 87.42, 87.27000000000001, 87.22999999999999, 87.35000000000001]
 Any[9.74, 11.32, 13.56, 18.16, 23.169999999999998, 28.389999999999997, 36.17, 47.65, 48.51, 51.480000000000004  …  95.78999999999999, 95.78, 95.83, 95.75, 95.81, 95.75, 95.72, 95.72, 95.72, 95.72]
 Any[9.74, 27.99, 45.58, 70.54, 71.25, 73.65, 79.59, 82.02000000000001, 77.63, 80.81  …  95.94, 95.73, 95.67, 95.75, 95.81, 95.93, 96.17, 96.15, 96.31, 96.28999999999999]
 Any[9.74, 11.43, 14.05, 18.22, 

In [162]:
p = plot(xlabel="iterations", ylabel="Accuracy test set (%)", legend=:bottom)
plot!(p, all_data[end].IterAccumulator, all_acc_test[end], label = all_legend[end])

# savefig(p, "graph_test_$(numberTest).svg")

p

<!DOCTYPE html>
 
 
 Plots.jl

## All comparaison

In [163]:
indices = [1,2,3,4,5,6,7]

7-element Array{Int64,1}:
 1
 2
 3
 4
 5
 6
 7

In [164]:
p_iter = plot(xlabel="iterations", ylabel="Accuracy test set (%)", xlims=(-5, 410), legend=:bottom)
for i in indices
    plot!(p_iter, all_data[i].IterAccumulator, all_acc_test[i], label = all_legend[i])
end
p_iter

# savefig(p_iter, "comparaison_all_methods_iter.svg")

p_iter

<!DOCTYPE html>
 
 
 Plots.jl

In [165]:
p_times = plot(xlabel="Time (s)", ylabel="Accuracy test set (%)", xlims=(-5, 110), legend=:bottom)
for i in indices
    plot!(p_times, all_data[i].Times, all_acc_test[i], label = all_legend[i])
end

# savefig(p_times, "comparaison_all_methods_times.svg")

p_times

<!DOCTYPE html>
 
 
 Plots.jl